# A Model of the Fed's View on Inflation

### Thomas Hasenzagl$^1$, Filippo Pellegrino$^2$, Lucrezia Reichlin$^3$, Giovanni Ricco$^4$

$^1$ University of Minnesota <br>
$^2$ London School of Economics and Political Science <br>
$^3$ London Business School, Now-Casting Economics, and CEPR <br>
$^4$ University of Warwick and OFCE-SciencesPo <br>


#### Notebook description

This notebook generates the charts and tables from the out-of-sample estimation exercise from the paper "A Model of the Fed's View on Inflation". Before running this notebook you have to run `user_main.jl` using `run_type=3`. 


In [1]:
# ----- Load libraries -----

using JLD;
using DataFrames, DataArrays;
include("./code/Metropolis-Within-Gibbs/MetropolisWithinGibbs.jl");
using MetropolisWithinGibbs;
using PlotlyJS;
using Rsvg;
pltjs = PlotlyJS;

INFO: Loading HttpServer methods...


In [2]:
oos_forecast = Array{Any}(4*(2016-1998+1)+3);
α_array      = Array{Any}(4*(2016-1998+1)+3);
σ_array      = Array{Any}(4*(2016-1998+1)+3);

start_i = 1;
end_i = 4;
for year=1998:2017
    if year != 2017
        println("res_$(year)_$(63+4*(year-1998))_oos.jld");
        res = load("res_$(year)_$(63+4*(year-1998))_oos.jld");
    else
        println("res_$(year)_$(63+4*(year-1998)-1)_oos.jld");
        res = load("res_$(year)_$(63+4*(year-1998)-1)_oos.jld");
    end
    j=1;
    for i=start_i:end_i
        oos_forecast[i] = res["oos_forecast"][j];
        α_array[i] = res["α_array"][j];
        σ_array[i] = res["σ_array"][j];
        j += 1;
    end
    
    if year != 2016
        start_i += 4;
        end_i += 4;    
    else
        start_i += 4;
        end_i += 3;
    end
end

res_1998_63_full.jld
res_1999_67_full.jld
res_2000_71_full.jld
res_2001_75_full.jld
res_2002_79_full.jld
res_2003_83_full.jld
res_2004_87_full.jld
res_2005_91_full.jld
res_2006_95_full.jld
res_2007_99_full.jld
res_2008_103_full.jld
res_2009_107_full.jld
res_2010_111_full.jld
res_2011_115_full.jld
res_2012_119_full.jld
res_2013_123_full.jld
res_2014_127_full.jld
res_2015_131_full.jld
res_2016_135_full.jld
res_2017_138_full.jld


In [3]:
# ----- Load data ----- 

res          = load("res_1998_60_oos.jld");
oos_forecast = res["oos_forecast"];
data         = res["data_full"];
date         = res["date"];
MNEMONIC     = res["MNEMONIC"];
α_array      = res["α_array"];
σ_array      = res["σ_array"];

# ----- Initial settings ----- 

end_presample_vec = [31, 12, 1998];
date_vec          = vcat([[Dates.day(date[i]) Dates.month(date[i]) Dates.year(date[i])] for i=1:length(date)]...);
start_oos         = find(sum(date_vec .== end_presample_vec', 2) .== 3)[1];
end_oos           = size(date_vec)[1];
max_h             = size(oos_forecast[1])[1];

In [4]:
# ----- Point forecasts, random walk forecasts -----

point_forecast = DataArray(zeros(size(oos_forecast)[1], size(data)[2], size(oos_forecast[1])[1]));
rw_forecast    = DataArray(zeros(size(oos_forecast)[1], size(data)[2], size(oos_forecast[1])[1]));
actual         = DataArray(zeros(size(oos_forecast)[1], size(data)[2], size(oos_forecast[1])[1]));

# Point forecast and random walk
for i = 1:size(oos_forecast)[1]
    d = mean(diff(data[1:start_oos+i-1,:]), 1)[:];
    for hz = 1:size(oos_forecast[1])[1]
        if hz == 1
            rw_forecast[i, :, hz] = d .+ data[start_oos+i-1, :];
        else
            rw_forecast[i, :, hz] = d .+ rw_forecast[i, :, hz-1]
        end
        
        point_forecast[i, :, hz] = median(oos_forecast[i][hz, :, :], 2);
    end
end

# Outturn
for i = start_oos:end_oos-size(oos_forecast[1])[1]
    for hz = 1:size(oos_forecast[1])[1]
        actual[i-start_oos+1, :, hz] = data[i+hz, :];
    end
end

# Remove the last hz observations since we don't have outcomes for them
actual         = actual[1: end-size(oos_forecast[1])[1], :, :];
point_forecast = point_forecast[1:end-size(oos_forecast[1])[1], :, :];
rw_forecast    = rw_forecast[1:end-size(oos_forecast[1])[1], :, :];

titles = ["Real GDP", "Employment", "Unemployment rate", "Oil price", "CPI inflation", "Core CPI inflation", "UOM: Expected inflation", "SPF: Expected CPI"];
scales = ["Bil. Chn. 2009\$", "Thousands", "Percent", "\$/Barrel", "Percent", "Percent", "Percent", "Percent"];

tc_rmsfe = sqrt(squeeze(mean((actual - point_forecast).^2, 1), 1));
rw_rmsfe = sqrt(squeeze(mean((actual - rw_forecast).^2, 1), 1));

writetable("./rmsfe.csv", DataFrame(tc_rmsfe./rw_rmsfe));

Stacktrace:
 [1] depwarn(::String, ::Symbol) at ./deprecated.jl:70
 [2] sqrt(::Base.ReshapedArray{Float64,2,DataArrays.DataArray{Float64,3},Tuple{}}) at ./deprecated.jl:57
 [3] include_string(::String, ::String) at ./loading.jl:522
 [4] execute_request(::ZMQ.Socket, ::IJulia.Msg) at /home/thomas/.julia/v0.6/IJulia/src/execute_request.jl:193
 [5] (::Compat.#inner#6{Array{Any,1},IJulia.#execute_request,Tuple{ZMQ.Socket,IJulia.Msg}})() at /home/thomas/.julia/v0.6/Compat/src/Compat.jl:189
 [6] eventloop(::ZMQ.Socket) at /home/thomas/.julia/v0.6/IJulia/src/eventloop.jl:8
 [7] (::IJulia.##13#16)() at ./task.jl:335
while loading In[4], in expression starting on line 43
Stacktrace:
 [1] depwarn(::String, ::Symbol) at ./deprecated.jl:70
 [2] sqrt(::Base.ReshapedArray{Float64,2,DataArrays.DataArray{Float64,3},Tuple{}}) at ./deprecated.jl:57
 [3] include_string(::String, ::String) at ./loading.jl:522
 [4] execute_request(::ZMQ.Socket, ::IJulia.Msg) at /home/thomas/.julia/v0.6/IJulia/src/execute_r

##### Stability of the common components

In [11]:
figures = Array{Any}(3);

c1 = "rgba(0, 48, 158, .75)"; 
c2 = "rgba(255, 0, 0, .75)";

titles_sub = ["Business Cycle", "Energy Price Cycle", "Common Trend"]
scales_sub = ["", "", ""];


for i=1:3
        
    traces1 = Array{Any}(length(α_array));

    for j=1:length(α_array)
        
        if i==1
            αij = median(α_array[j][1,:,:], 2); #αij = median(α_array[j][1,:,:]+α_array[j][2,:,:]+α_array[j][3,:,:], 2);
        elseif i==2
            αij = median(α_array[j][4,:,:], 2); #αij = median(α_array[j][4,:,:]+α_array[j][5,:,:], 2);
        elseif i==3
            αij = median(α_array[j][6,:,:], 2);
        end
        
        traces1[j] = pltjs.scatter(x=date[1:end-max_h], y=αij[1:end-max_h], name="State", mode="lines", line=attr(width=1), showlegend=false);
    end
    
    traces1 = convert(Array{PlotlyJS.GenericTrace{Dict{Symbol,Any}},1}, traces1)

    layout  = pltjs.Layout(;title=titles_sub[i], titlefont=attr(size=12),
                           xaxis=attr(tickfont_size=10, showgrid=true, linecolor="black", mirror=true, nticks=20, tickangle=-90, zeroline=false),
                           yaxis=attr(tickfont_size=10, showgrid=true, linecolor="black", mirror=true, zeroline=false, titlefont=attr(size=10), title=scales_sub[i]));

    figures[i] = pltjs.plot(traces1, layout);
end

fig = [figures[1]; figures[2]; figures[3]];

# Size
fig.plot.layout["width"]  = 800;
fig.plot.layout["height"] = 600;

# Margins
fig.plot.layout["margin"][:b]  = 40;
fig.plot.layout["margin"][:t]  = 40;
fig.plot.layout["margin"][:r]  = 40;
fig.plot.layout["margin"][:l]  = 40;

# Title size
for i=1:3
    fig.plot.layout["annotations"][i][:font][:size] = 12;
end

pltjs.savefig(fig, "./img/factor_revisions.eps")

